# This notebook will be mainly used for the capstone project


### Import Library

In [95]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
!conda install -c conda-forge geopy --yes
import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage


#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


### Scraping Data From Wikipedia

In [96]:
headers = {
    'Access-Control-Allow-Origin': '*',
    'Access-Control-Allow-Methods': 'GET',
    'Access-Control-Allow-Headers': 'Content-Type',
    'Access-Control-Max-Age': '3600',
    'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:52.0) Gecko/20100101 Firefox/52.0'
    }

url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
req = requests.get(url, headers)
soup = BeautifulSoup(req.content, 'html.parser')

### Pre-Processing Data

In [97]:
table= soup.find("table")
table
table_rows = table.find_all('tr')
res = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
     
        res.append(row)


df = pd.DataFrame(res, columns=["Postal Code", "Borough", "Neighborhood"])

df = df[df.Borough != 'Not assigned']

In [4]:
df = df.groupby(['Postal Code','Borough'])['Neighborhood'].apply(', '.join).reset_index()
df.head(10)
#change column order                           


Postal Code      Borough                                     Neighborhood
0         M1B  Scarborough                                   Malvern, Rouge
1         M1C  Scarborough           Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough                Guildwood, Morningside, West Hill
3         M1G  Scarborough                                           Woburn
4         M1H  Scarborough                                        Cedarbrae
5         M1J  Scarborough                              Scarborough Village
6         M1K  Scarborough      Kennedy Park, Ionview, East Birchmount Park
7         M1L  Scarborough                  Golden Mile, Clairlea, Oakridge
8         M1M  Scarborough  Cliffside, Cliffcrest, Scarborough Village West
9         M1N  Scarborough                      Birch Cliff, Cliffside West

In [20]:
df.shape



(103, 5)

### create  dataframe With Geo Locations 

In [98]:
df['latitude']=''
df['longitude']=''
import geocoder # import geocoder
# initialize your variable to None
for ind in df.index: 
     postal_code=  df['Postal Code'][ind]
     lat_lng_coords = None
   
    # loop until you get the coordinates
     while(lat_lng_coords is None):
  #    print(postal_code)
      #print('Toronto, Ontario'.format(postal_code))
      #g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
      g = geocoder.arcgis('{}, Toronto, Ontario'.format(postal_code)) 
      lat_lng_coords = g.latlng
      #print("postal_code:"+postal_code+" lat_lng_coords:"+str(lat_lng_coords)+"")  
     df['latitude'][ind] = lat_lng_coords[0]
     df['longitude'][ind] = lat_lng_coords[1]      
df.head()
        


Postal Code           Borough                                 Neighborhood  \
2         M3A        North York                                    Parkwoods   
3         M4A        North York                             Victoria Village   
4         M5A  Downtown Toronto                    Regent Park, Harbourfront   
5         M6A        North York             Lawrence Manor, Lawrence Heights   
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

  latitude longitude  
2  43.7529  -79.3356  
3  43.7281  -79.3119  
4   43.651   -79.353  
5  43.7233  -79.4512  
6  43.6618  -79.3894

# 2. Explore Neighborhoods in Toronto

In [ ]:
CLIENT_ID = 'TYMN3CEHGGSFPQVFFINE2DZIBP5FOM1NUTWTN1J3U5ITGGCF' # your Foursquare ID
CLIENT_SECRET = '2YIBTV3F001GZNR5X1KS2KGX0ZG5JAUQMFEDCXW15C3ICJ3S' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

In [99]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        print(results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [47]:
toronto_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['latitude'],
                                   longitudes=df['longitude']
                                  )

Malvern, Rouge
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5561eacb498e09ff53b397ad', 'name': 'Upper Rouge Trail', 'location': {'lat': 43.809988, 'lng': -79.186147, 'labeledLatLngs': [{'label': 'display', 'lat': 43.809988, 'lng': -79.186147}], 'distance': 338, 'cc': 'CA', 'country': 'Canada', 'formattedAddress': ['Canada']}, 'categories': [{'id': '4bf58dd8d48988d159941735', 'name': 'Trail', 'pluralName': 'Trails', 'shortName': 'Trail', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/hikingtrail_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-5561eacb498e09ff53b397ad-0'}]
Rouge Hill, Port Union, Highland Creek
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4e3ddf2bb61cb577be7e1844', 'name': 'Fox and Fi

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4cc1d28c06c254815ac18547', 'name': 'Starbucks', 'location': {'address': '300 Borough Dr', 'crossStreet': 'Scarborough Town Centre', 'lat': 43.770037201625215, 'lng': -79.22115586641958, 'labeledLatLngs': [{'label': 'display', 'lat': 43.770037201625215, 'lng': -79.22115586641958}], 'distance': 295, 'cc': 'CA', 'city': 'Scarborough', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['300 Borough Dr (Scarborough Town Centre)', 'Scarborough ON', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d1e0931735', 'name': 'Coffee Shop', 'pluralName': 'Coffee Shops', 'shortName': 'Coffee Shop', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/coffeeshop_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4cc1d28c06c254815ac18547-0'}, {'reasons': {'count': 0, 'items': [{'summary': '

KeyboardInterrupt: 

In [ ]:
toronto_venues.shape


In [ ]:
toronto_venues.head()

In [100]:
# create map of Toronto using latitude and longitude values
import folium # map rendering library
map_toronto = folium.Map(location=[43.651070, -79.347015], zoom_start=11)

# add markers to map
for lat, lng, label in zip(toronto_venues['Venue Latitude'], toronto_venues['Venue Longitude'], toronto_venues['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [48]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 273 uniques categories.


In [101]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
#fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])


first_col = toronto_onehot.pop("Neighborhood")
toronto_onehot.insert(0, "Neighborhood", first_col)
#print(toronto_onehot.columns.get_loc("Neighborhood") )
toronto_onehot.head()



Neighborhood  ATM  Accessories Store  \
0                          Malvern, Rouge    0                  0   
1  Rouge Hill, Port Union, Highland Creek    0                  0   
2       Guildwood, Morningside, West Hill    0                  0   
3       Guildwood, Morningside, West Hill    0                  0   
4       Guildwood, Morningside, West Hill    0                  0   

   Afghan Restaurant  Airport  American Restaurant  Art Gallery  Art Museum  \
0                  0        0                    0            0           0   
1                  0        0                    0            0           0   
2                  0        0                    0            0           0   
3                  0        0                    0            0           0   
4                  0        0                    0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Badminton Court  \
0            0              0          0           0                0   
1            0              0          0           0                0   
2            0              0          0           0                0   
3            0              0          0           0                0   
4            0              0          0           0                0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0           0       0     0    0               0                 0   
1           0       0     0    1               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Stadium  Beach Bar  Beer Bar  Beer Store  Belgian Restaurant  \
0                   0          0         0           0                   0   
1                   0          0         0           0                   0   
2                   0          0         0           0                   0   
3                   0          0         0           0                   0   
4                   0          0         0           0                   0   

   Big Box Store  Bike Shop  Bistro  Board Shop  Bookstore  Boutique  \
0              0          0       0           0          0         0   
1              0          0       0           0          0         0   
2              0          0       0           0          0         0   
3              0          0       0           0          0         0   
4              0          0       0           0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0               0        0            0       0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0             0              0         0   
2                0         0             0              0         0   
3                0         0             0              0         0   
4                0         0             0              0         0   

   Bus Station  Bus Stop

In [69]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  ATM  Accessories Store  \
0                                           Agincourt  0.0           0.000000   
1                              Alderwood, Long Branch  0.0           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North  0.0           0.000000   
3                                     Bayview Village  0.0           0.000000   
4                   Bedford Park, Lawrence Manor East  0.0           0.000000   
5                                         Berczy Park  0.0           0.000000   
6                         Birch Cliff, Cliffside West  0.0           0.000000   
7        Brockton, Parkdale Village, Exhibition Place  0.0           0.022727   
8   Business reply mail Processing Centre, South C...  0.0           0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...  0.0           0.000000   
10                                Caledonia-Fairbanks  0.0           0.000000   
11              Canada Post Gateway Processing Centre  0.0           0.000000   
12                                          Cedarbrae  0.0           0.000000   
13                                 Central Bay Street  0.0           0.000000   
14                                           Christie  0.0           0.000000   
15                               Church and Wellesley  0.0           0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan  0.0           0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West  0.0           0.000000   
18                     Commerce Court, Victoria Hotel  0.0           0.000000   
19                                         Davisville  0.0           0.000000   
20                                   Davisville North  0.0           0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn  0.0           0.000000   
22                                          Don Mills  0.0           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...  0.0           0.000000   
24                                          Downsview  0.0           0.000000   
25                       Dufferin, Dovercourt Village  0.0           0.000000   
26      East Toronto, Broadview North (Old East York)  0.0           0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...  0.0           0.000000   
28                       Fairview, Henry Farm, Oriole  0.0           0.000000   
29             First Canadian Place, Underground city  0.0           0.000000   
..                                                ...  ...                ...   
68             Rouge Hill, Port Union, Highland Creek  0.0           0.000000   
69                                 Runnymede, Swansea  0.0           0.000000   
70                      Runnymede, The Junction North  0.0           0.000000   
71                                Scarborough Village  0.0           0.000000   
72  South Steeles, Silverstone, Humbergate, Jamest...  0.0           0.000000   
73                                     St. James Town  0.0           0.000000   
74                        St. James Town, Cabbagetown  0.0           0.000000   
75                      Steeles West, L'Amoreaux West  0.0           0.000000   
76                                     Stn A PO Boxes  0.0           0.000000   
77                                    Studio District  0.0           0.000000   
78  Summerhill West, Rathnelly, South Hill, Forest...  0.0           0.000000   
79                The Annex, North Midtown, Yorkville  0.0           0.000000   
80                                        The Beaches  0.0           0.000000   
81                       The Danforth West, Riverdale  0.0           0.000000   
82      The Kingsway, Montgomery Road, Old Mill North  0.0           0.000000   
83                                   Thorncliffe Park  0.0           0.000000   
84           Toronto Dominion Centre, Design Exchange  0.0           0.000000   
85                     University of Toronto, Harbord  0.0           0.0

In [104]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
              venue  freq
0  Sushi Restaurant   0.2
1    Breakfast Spot   0.2
2   Badminton Court   0.2
3       Supermarket   0.2
4      Skating Rink   0.2


----Alderwood, Long Branch----
            venue  freq
0     Pizza Place  0.11
1    Dance Studio  0.11
2  Sandwich Place  0.11
3     Gas Station  0.11
4             Gym  0.11


----Bathurst Manor, Wilson Heights, Downsview North----
                 venue  freq
0                 Bank  0.10
1          Coffee Shop  0.10
2  Fried Chicken Joint  0.05
3          Pizza Place  0.05
4        Deli / Bodega  0.05


----Bayview Village----
                        venue  freq
0                       Trail  0.33
1  Construction & Landscaping  0.33
2                 Flower Shop  0.33
3                         ATM  0.00
4                      Museum  0.00


----Bedford Park, Lawrence Manor East----
                venue  freq
0    Sushi Restaurant  0.10
1      Sandwich Place  0.10
2         Coffee Shop  0.10
3  Italian Restaura

4                      Music Venue   0.0


----Humberlea, Emery----
                 venue  freq
0           Playground   0.5
1                 Park   0.5
2               Museum   0.0
3        Movie Theater   0.0
4  Moroccan Restaurant   0.0


----Humewood-Cedarvale----
           venue  freq
0   Hockey Arena  0.17
1           Park  0.17
2          Field  0.17
3  Grocery Store  0.17
4          Trail  0.17


----India Bazaar, The Beaches West----
                  venue  freq
0        Sandwich Place  0.10
1                  Park  0.10
2  Fast Food Restaurant  0.10
3         Burrito Place  0.05
4         Movie Theater  0.05


----Islington Avenue, Humber Valley Village----
                     venue  freq
0                     Park  0.50
1           Baseball Field  0.25
2             Skating Rink  0.25
3  New American Restaurant  0.00
4                   Museum  0.00


----Kennedy Park, Ionview, East Birchmount Park----
                venue  freq
0      Discount Store   0.2
1         Co

                 venue  freq
0          Coffee Shop  0.07
1                Hotel  0.05
2           Taco Place  0.03
3  Japanese Restaurant  0.03
4                 Café  0.03


----Studio District----
                 venue  freq
0         Night Market  0.33
1       Baseball Field  0.33
2  Government Building  0.33
3                  ATM  0.00
4          Music Venue  0.00


----Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park----
                venue  freq
0  Light Rail Station  0.29
1         Coffee Shop  0.29
2         Supermarket  0.14
3        Skating Rink  0.14
4        Liquor Store  0.14


----The Annex, North Midtown, Yorkville----
            venue  freq
0            Café  0.13
1  Sandwich Place  0.09
2     Pizza Place  0.04
3       BBQ Joint  0.04
4    Burger Joint  0.04


----The Beaches----
               venue  freq
0              Trail   0.2
1                Pub   0.2
2  Health Food Store   0.2
3             Church   0.2
4        Music Venue   0.0


----Th

In [103]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [105]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt        Breakfast Spot   
1                           Alderwood, Long Branch              Pharmacy   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village           Flower Shop   
4                Bedford Park, Lawrence Manor East    Italian Restaurant   

        2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                 Supermarket       Badminton Court          Skating Rink   
1                         Pub           Pizza Place        Sandwich Place   
2                 Coffee Shop        Sandwich Place        Ice Cream Shop   
3  Construction & Landscaping                 Trail  Fast Food Restaurant   
4                 Coffee Shop        Sandwich Place      Sushi Restaurant   

  5th Most Common Venue    6th Most Common Venue 7th Most Common Venue  \
0      Sushi Restaurant                  Dog Run            Donut Shop   
1          Dance Studio              Coffee Shop                   Gym   
2     Mobile Phone Shop      Fried Chicken Joint                 Diner   
3                 Field           Farmers Market                  Farm   
4              Pharmacy  Comfort Food Restaurant            Restaurant   

  8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
0   Dumpling Restaurant  Eastern European Restaurant      Electronics Store  
1     Convenience Store                  Gas Station         Discount Store  
2            Restaurant    Middle Eastern Restaurant            Gas Station  
3    Falafel Restaurant         Ethiopian Restaurant         Discount Store  
4                   Pub                         Café            Sports Club

## 4. Cluster Neighborhoods

In [106]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit( toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 1, 3, 3, 3, 3, 3, 3, 3, 3])

In [112]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  \
0                          Malvern, Rouge              43.808626   
1  Rouge Hill, Port Union, Highland Creek              43.785779   
2       Guildwood, Morningside, West Hill              43.765806   
3       Guildwood, Morningside, West Hill              43.765806   
4       Guildwood, Morningside, West Hill              43.765806   

   Neighborhood Longitude                 Venue  Venue Latitude  \
0              -79.189913     Upper Rouge Trail       43.809988   
1              -79.157368        Fox and Fiddle       43.789082   
2              -79.185284           Chick-N-Joy       43.768752   
3              -79.185284  Little Caesars Pizza       43.769046   
4              -79.185284          Swiss Chalet       43.768122   

   Venue Longitude       Venue Category  Cluster Labels 1st Most Common Venue  \
0       -79.186147                Trail               2                 Trail   
1       -79.154459                  Bar               3                   Bar   
2       -79.187982  Fried Chicken Joint               1  Fast Food Restaurant   
3       -79.184386          Pizza Place               1  Fast Food Restaurant   
4       -79.190493           Restaurant               1  Fast Food Restaurant   

  2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
0           Yoga Studio       Doctor's Office                 Dog Run   
1           Yoga Studio     Elementary School                 Dog Run   
2           Pizza Place           Coffee Shop  Thrift / Vintage Store   
3           Pizza Place           Coffee Shop  Thrift / Vintage Store   
4           Pizza Place           Coffee Shop  Thrift / Vintage Store   

  5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
0            Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
1            Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
2   Fried Chicken Joint            Beer Store                   Restaurant   
3   Fried Chicken Joint            Beer Store                   Restaurant   
4   Fried Chicken Joint            Beer Store                   Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0     Electronics Store     Elementary School         Discount Store  
1     Electronics Store  Ethiopian Restaurant            Flower Shop  
2                  Bank            Laundromat             Sports Bar  
3                  Bank            Laundromat             Sports Bar  
4                  Bank            Laundromat             Sports Bar

In [113]:
# create map
map_clusters = folium.Map(location=[43.651070, -79.347015], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters